# Manutenzione preventiva - 

# Manutenzione preventiva - DoS Attacks

In [46]:
import pandas as pd
import json as json
import ipaddress as ip 
import numpy as np
import functions_notebook as fn
import costants as cs
import warnings
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import accuracy_score
from sklearn.impute import SimpleImputer
from sklearn.svm import SVC
warnings.simplefilter(action='ignore', category=FutureWarning)

In [47]:
data_cc_1_05h= fn.open_convert_capture(".\\captures\\captures1_v2\\clean\\eth2dump-clean-0,5h_1.json")


data_pf_att_1m_30m_1 = fn.open_convert_capture("C:\\Users\\User\\Desktop\\manprev2324\\manprev2324\\captures\\captures1_v2\\pingFloodDDoS\\eth2dump-pingFloodDDoS5m-1h_1.json")
data_pf_att_1m_30m_2 = fn.open_convert_capture("C:\\Users\\User\\Desktop\\manprev2324\\manprev2324\\captures\\captures1_v2\\pingFloodDDoS\\eth2dump-pingFloodDDoS5m-1h_1.json")
data_pf_att_1m_30m_3 = fn.open_convert_capture("C:\\Users\\User\\Desktop\\manprev2324\\manprev2324\\captures\\captures1_v2\\pingFloodDDoS\\eth2dump-pingFloodDDoS5m-1h_1.json")

In [48]:
pv_cc_1_05h = fn.create_array_values(data_cc_1_05h)


pv_pf_att_1m_30m_1 = fn.create_array_values(data_pf_att_1m_30m_1)
pv_pf_att_1m_30m_2 = fn.create_array_values(data_pf_att_1m_30m_2)
pv_pf_att_1m_30m_3 = fn.create_array_values(data_pf_att_1m_30m_3)

In [49]:
print(len(cs.df_columns))

67


In [82]:
# Costruzione dataframe
# Conversione colonna timestamp a float
# Inserimento colonna inter packet arrival time
# Cattura clean 30m_1
df_cc_30m_1 = pd.DataFrame(data=pv_cc_1_05h, columns=cs.df_columns)




# Catture pf att 1m 30m
df1_pfatt_1m_30m_1 = pd.DataFrame(pv_pf_att_1m_30m_1, columns=cs.df_columns)
df1_pfatt_1m_30m_1['frame.time_epoch'] = df1_pfatt_1m_30m_1['frame.time_epoch'].astype('float')
df1_pfatt_1m_30m_1[cs.ipat_field_name] = df1_pfatt_1m_30m_1['frame.time_epoch'].diff()
df2_pfatt_1m_30m_2 = pd.DataFrame(pv_pf_att_1m_30m_2, columns=cs.df_columns)
df2_pfatt_1m_30m_2['frame.time_epoch'] = df2_pfatt_1m_30m_2['frame.time_epoch'].astype('float')
df2_pfatt_1m_30m_2[cs.ipat_field_name] = df2_pfatt_1m_30m_2['frame.time_epoch'].diff()
df3_pfatt_1m_30m_3 = pd.DataFrame(pv_pf_att_1m_30m_3, columns=cs.df_columns)
df3_pfatt_1m_30m_3['frame.time_epoch'] = df3_pfatt_1m_30m_3['frame.time_epoch'].astype('float')
df3_pfatt_1m_30m_3[cs.ipat_field_name] = df3_pfatt_1m_30m_3['frame.time_epoch'].diff()

# Concatenazione per righe
df_pfatt_1m_30m = pd.concat([df1_pfatt_1m_30m_1, df2_pfatt_1m_30m_2, df3_pfatt_1m_30m_3], ignore_index=True)


In [83]:
df_p_cc_05h=fn.clean_df(df_cc_30m_1)
df_pfatt_1m_30m = fn.clean_df(df_pfatt_1m_30m)

In [84]:
df_p_cc_05h

df_p_cc_05h['frame.time_epoch'] = df_p_cc_05h['frame.time_epoch'].astype('float')
df_p_cc_05h[cs.ipat_field_name] = df_p_cc_05h['frame.time_epoch'].diff()
print(df_pfatt_1m_30m['frame.time_epoch'])
'''df_pfatt_1m_30m['frame.time_epoch'] = df_pfatt_1m_30m['frame.time_epoch'].astype('float')
df_pfatt_1m_30m[cs.ipat_field_name] = df_pfatt_1m_30m['frame.time_epoch'].diff()'''


0         1.526908e+09
1         1.526908e+09
2         1.526908e+09
3         1.526908e+09
4         1.526908e+09
              ...     
286132    1.526911e+09
286133    1.526911e+09
286134    1.526911e+09
286135    1.526911e+09
286136    1.526911e+09
Name: frame.time_epoch, Length: 286137, dtype: float64


"df_pfatt_1m_30m['frame.time_epoch'] = df_pfatt_1m_30m['frame.time_epoch'].astype('float')\ndf_pfatt_1m_30m[cs.ipat_field_name] = df_pfatt_1m_30m['frame.time_epoch'].diff()"

In [85]:
df_p_cc_05h['frame.time_epoch'] = pd.to_datetime(df_p_cc_05h['frame.time_epoch'], unit='s')
df_pfatt_1m_30m['frame.time_epoch'] = pd.to_datetime(df_pfatt_1m_30m['frame.time_epoch'], unit='s')


In [86]:
import pandas as pd

df_p_cc_05h['label'] = 0
df_pfatt_1m_30m['label'] = 1

df_p_cc_05h['capture_id'] = (df_p_cc_05h['frame.time_epoch'].diff() > pd.Timedelta(seconds=0.1)).cumsum()
df_pfatt_1m_30m['capture_id'] = (df_pfatt_1m_30m['frame.time_epoch'].diff() > pd.Timedelta(seconds=0.1)).cumsum()


df_p_cc_05h['frame.time_epoch_numeric'] = df_p_cc_05h['frame.time_epoch'].astype('int64') // 10**9
df_pfatt_1m_30m['frame.time_epoch_numeric'] = df_pfatt_1m_30m['frame.time_epoch'].astype('int64') // 10**9


df_p_cc_05h = df_p_cc_05h.drop(columns=['frame.time_epoch'])

df_pfatt_1m_30m = df_pfatt_1m_30m.drop(columns=['frame.time_epoch'])

concat = pd.concat([df_p_cc_05h, df_pfatt_1m_30m], axis=0)
non_numeric_columns = concat.select_dtypes(exclude=['number']).columns




concat_grouped = concat.groupby(['capture_id', 'label']).sum(numeric_only=True).reset_index()
numero_gruppi_df_concatenato = len(concat_grouped)
print(f"Numero di gruppi nel DataFrame concatenato e raggruppato (Metodo 1): {numero_gruppi_df_concatenato}")

print(concat_grouped.columns)



Numero di gruppi nel DataFrame concatenato e raggruppato (Metodo 1): 27645
Index(['capture_id', 'label', 'eth.type', 'eth.len', 'arp.hw.type',
       'arp.proto.type', 'arp.hw.size', 'arp.proto.size', 'icmp.type',
       'icmp.code', 'icmp.checksum', 'icmp.checksum.status', 'ip.version',
       'ip.hdr_len', 'ip.dsfield', 'ip.len', 'ip.id', 'ip.flags', 'ip.ttl',
       'ip.proto', 'ip.checksum', 'ip.checksum.status', 'ip.src', 'ip.dst',
       'tcp.srcport', 'tcp.dstport', 'tcp.stream', 'tcp.len', 'tcp.seq',
       'tcp.nxtseq', 'tcp.ack', 'tcp.hdr_len', 'tcp.flags',
       'tcp.window_size_value', 'tcp.window_size', 'tcp.checksum',
       'tcp.checksum.status', 'tcp.urgent_pointer', 'udp.srcport',
       'udp.dstport', 'udp.port', 'udp.length', 'udp.checksum',
       'udp.checksum_status', 'mbtcp.trans_id', 'mbtcp.prot_id', 'mbtcp.len',
       'mbtcp.unit_id', 'ip.flags.rb', 'ip.flags.df', 'ip.flags.mf',
       'tcp.flags.res', 'tcp.flags.ae', 'tcp.flags.cwr', 'tcp.flags.urg',
       

In [87]:
concat_grouped['label']
X = concat_grouped.drop(['label', 'capture_id'], axis=1)


imputer = SimpleImputer(strategy='mean')
X_imputed = pd.DataFrame(imputer.fit_transform(X), columns=X.columns)


X_train, X_test, y_train, y_test = train_test_split(X_imputed, y, test_size=0.30, random_state=42, stratify=y)


scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

svm_model = SVC(kernel='rbf', C=10.0, gamma='scale')
svm_model.fit(X_train, y_train)

y_pred = svm_model.predict(X_test)

for i in range(len(y_test)):
    print(f"Elemento {i + 1}:")
    print(f"  Caratteristiche: {X_test[i]}")
    print(f"  Classe prevista: {y_pred[i]}")
    print(f"  Classe effettiva: {y_test.values[i]}\n")


print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

print("\nClassification Report:")
print(classification_report(y_test, y_pred))


Elemento 1:
  Caratteristiche: [-0.01516819 -0.16171407 -0.12627457 -0.12627457 -0.12627457 -0.12627457
 -0.01016683  0.         -0.01016683 -0.01016683 -0.01403499 -0.01403533
 -0.12549066 -0.01474434 -0.01456094 -0.09407206 -0.01652246 -0.02958244
 -0.01298938 -0.01403499 -0.01639886 -0.01500601 -0.11031469 -0.10715539
 -0.42019631  0.60434164  2.27179052  2.27170493  2.31995968 -0.09743963
 -0.09043988  0.51890024  0.51890024 -0.12590578 -0.09695629  0.
 -0.06594745 -0.0522744  -0.0522744  -0.10466528 -0.1319969   0.
 -0.15542384  0.          1.00172861  0.65850127 -0.14510878 -0.09750115
  0.         -0.01020746  0.         -0.01017218 -0.01020746 -0.09134148
 -0.07874474 -0.15542384 -0.15699141 -0.09695629  0.          0.
 -0.09695629 -0.09695629  0.          0.65850127 -0.12194189 -0.15859689
 -0.06727105 -0.01499903]
  Classe prevista: 0
  Classe effettiva: 0

Elemento 2:
  Caratteristiche: [-0.01985798  0.45127888 -0.12627457 -0.12627457 -0.12627457 -0.12627457
 -0.01016683  0.

In [88]:
from sklearn.model_selection import cross_val_score

scores = cross_val_score(svm_model, X_train, y_train, cv=5)
print("Cross-validation scores:", scores)

Cross-validation scores: [0.9958667  0.99767442 0.99689922 0.99560724 0.99664083]
